In [1]:
import torch
from pytorch_pretrained_bert import BertTokenizer
from pytorch_pretrained_bert.modelingold import BertModel
from pytorch_pretrained_bert.modelingold import BertForSimpleRelationExtraction, BertConfig, BertForSimpleRelationExtraction_allwords, BertForEntityandRelation_entrelsametime_ver2_negsen, BertForEntityandRelation_entrelsametime_ver2_negsen_last
import argparse
from pytorch_pretrained_bert.file_utils import PYTORCH_PRETRAINED_BERT_CACHE
from pytorch_pretrained_bert.optimization import BertAdam, warmup_linear
from tqdm import tqdm, trange
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler
from torch.utils.data.distributed import DistributedSampler
import os
import random
from torch.nn import MSELoss

In [2]:
def subfinder(mylist, pattern):
    matches = []
    idx_list = []
    for i in range(len(mylist)):
        if mylist[i] == pattern[0] and mylist[i:i+len(pattern)] == pattern:
            matches.append(pattern)
            idx_list.append((i, i+len(pattern)))
    return idx_list

In [3]:
def dataset_id2emb_genfun(pathtodataset):
    relidx2id = {}
    with open(pathtodataset + 'rel2id.txt' , mode = 'r') as f:
        for idx,line in enumerate(f):
            tmp = line.split('\t')
            relidx2id[idx] =tmp[1][:-1]
    relid2emb = {}
    with open(pathtodataset + 'relation2vec.txt' , mode = 'r') as f:
        for idx,line in enumerate(f):
            tmp = line[:-1].split()
            relemb = []
            for sc in tmp:
                relemb.append(float(sc))
            id_c = relidx2id[idx]
            if not id_c in relid2emb:
                relid2emb[relidx2id[idx]] = relemb
    return relid2emb

In [4]:
def dataset_gen_instance_fun(pathtodataset, kb_id2emb, modefile):
    bag = []
    with open(pathtodataset + modefile , mode = 'r', encoding = 'utf-8') as f:
        for line in f:
            tmp = line[:-1].split('\t')
            if tmp[2] in kb_id2emb:
                bag.append((tmp[6], tmp[2], tmp[3], tmp[4],1))
    return bag

In [5]:
def negative_examples_gen(pathtodataset, kb_id2emb, modefile, randf):
    mode = modefile.split('_')[0]
    bag = []
    beverb = ["be", "am", "is", "are", "was", "were"]
    helpverb = ["have", "has", "had", "could", "should", "would", "may", "might", "must", "shall", "can", "will", "do", "did", "does"]
    #일정 확률로 이 data넣기
    with open(pathtodataset + mode + '_align_all.tsv', mode = 'r') as f:
        for line in f:
            randn = random.random()
            if (randn < randf):
                heflag = 0
                fuzzyweight = 1
                tmp = line[:-1].split('\t')
                if tmp[2] in kb_id2emb:
                    rel = tmp[5].split(' ')
                    
                    if (randn < randf/4):
                        fuzzyweight = -1
                        for hev in helpverb:
                            if hev in rel:
                                rel[rel.index(hev)] = hev + ' not'
                                heflag = 1
                                break
                        if (heflag == 0):
                            for bev in beverb:
                                if bev in rel:
                                    rel[rel.index(bev)] = bev + ' not'
                                    heflag = 1
                                    break
                        if (heflag == 0):
                            rel[0] = rel[0] + ' not'
                    
                    elif (randn < randf/2):
                        fuzzyweight = 0.6
                        if (heflag == 0):
                            for bev in beverb:
                                if bev in rel:
                                    rel[rel.index(bev)] = 'may'
                                    heflag = 1
                                    break
                        if (heflag == 0):
                            rel[0] = 'may ' + rel[0]
                    
                    elif (randn < (randf/4) * 3):
                        fuzzyweight = 0.8
                        if (heflag == 0):
                            for bev in beverb:
                                if bev in rel:
                                    rel[rel.index(bev)] = 'should'
                                    heflag = 1
                                    break
                        if (heflag == 0):
                            rel[0] = 'should ' + rel[0]
                    else:
                        fuzzyweight = 0.9
                        if (heflag == 0):
                            for bev in beverb:
                                if bev in rel:
                                    rel[rel.index(bev)] = 'must'
                                    heflag = 1
                                    break
                        if (heflag == 0):
                            rel[0] = 'must ' + rel[0]
                    
                    tmp[5] = ' '.join(rel)
                    bag.append((' '.join(tmp[4:7]), tmp[2], tmp[4], tmp[6],fuzzyweight))
    return bag

In [6]:
parser = argparse.ArgumentParser()

In [7]:
parser.add_argument("--bert_model", default=None, type=str, required=True,help="Bert pre-trained model selected in the list: bert-base-uncased, ""bert-large-uncased, bert-base-cased, bert-large-cased, bert-base-multilingual-uncased, ""bert-base-multilingual-cased, bert-base-chinese.")
parser.add_argument("--output_dir", default=None, type=str, required=True, help="The output directory where the model checkpoints and predictions will be written.")
parser.add_argument("--train_file", default=None, type=str, help="SQuAD json for training. E.g., train-v1.1.json")
parser.add_argument("--predict_file", default=None, type=str,help="SQuAD json for predictions. E.g., dev-v1.1.json or test-v1.1.json")
parser.add_argument("--max_seq_length", default=384, type=int,help="The maximum total input sequence length after WordPiece tokenization. Sequences ""longer than this will be truncated, and sequences shorter than this will be padded.")
parser.add_argument("--do_train", action='store_true', help="Whether to run training.")
parser.add_argument("--do_predict", action='store_true', help="Whether to run eval on the dev set.")
parser.add_argument("--train_batch_size", default=32, type=int, help="Total batch size for training.")
parser.add_argument("--predict_batch_size", default=8, type=int, help="Total batch size for predictions.")
parser.add_argument("--learning_rate", default=5e-5, type=float, help="The initial learning rate for Adam.")
parser.add_argument("--num_train_epochs", default=3.0, type=float,help="Total number of training epochs to perform.")
parser.add_argument("--warmup_proportion", default=0.1, type=float,help="Proportion of training to perform linear learning rate warmup for. E.g., 0.1 = 10%% ""of training.")
parser.add_argument("--verbose_logging", action='store_true',help="If true, all of the warnings related to data processing will be printed. ""A number of warnings are expected for a normal SQuAD evaluation.")
parser.add_argument("--no_cuda",action='store_true',help="Whether not to use CUDA when available")
parser.add_argument('--seed',type=int,default=42,help="random seed for initialization")
parser.add_argument('--gradient_accumulation_steps',type=int,default=1,help="Number of updates steps to accumulate before performing a backward/update pass.")
parser.add_argument("--do_lower_case", action='store_true',help="Whether to lower case the input text. True for uncased models, False for cased models.")
parser.add_argument("--local_rank",type=int,default=-1,help="local_rank for distributed training on gpus")
parser.add_argument('--null_score_diff_threshold',type=float, default=0.0,help="If null_score - best_non_null is greater than the threshold predict null.")
parser.add_argument('--rel_dim',type=int, default=200,help="Size of KB relation embedding")
parser.add_argument('--datapath',type=str, default=None,help="Path to datafolder")
parser.add_argument('--traindataname',type=str, default=None,help="name of traindata")
parser.add_argument('--devdataname',type=str, default=None,help="name of traindata")
parser.add_argument('--testdataname',type=str, default=None,help="name of traindata")

_StoreAction(option_strings=['--testdataname'], dest='testdataname', nargs=None, const=None, default=None, type=<class 'str'>, choices=None, help='name of traindata', metavar=None)

In [8]:
args = parser.parse_args(["--bert_model", "bert-base-uncased","--output_dir", "./output_entityrelation_relentsame_ver2_negsen2_masked_0.9","--do_train","--do_lower_case", "--train_batch_size","10","--max_seq_length","128","--rel_dim","200","--datapath","./dataset/","--traindataname","train_sentences.tsv","--devdataname","valid_sentences.tsv","--testdataname","test_sentences.tsv"])

In [9]:
tokenizer = BertTokenizer.from_pretrained(args.bert_model)

In [10]:
kb_id2emb = dataset_id2emb_genfun(args.datapath)
train_bag = dataset_gen_instance_fun(args.datapath,kb_id2emb,args.traindataname)
dev_bag = dataset_gen_instance_fun(args.datapath,kb_id2emb,args.devdataname)
test_bag = dataset_gen_instance_fun(args.datapath,kb_id2emb,args.testdataname)

In [11]:
train_bag_neg = negative_examples_gen(args.datapath,kb_id2emb,args.traindataname, 0.005)
dev_bag_neg = negative_examples_gen(args.datapath,kb_id2emb,args.devdataname, 0.005)
test_bag_neg = negative_examples_gen(args.datapath,kb_id2emb,args.testdataname, 0.005)

In [12]:
relid2idx = {}
idx2relid = {}
for idx, relid in enumerate(kb_id2emb):
    relid2idx[relid] = idx
    idx2relid[idx] = relid

In [13]:
device = torch.device("cuda" if torch.cuda.is_available() and not args.no_cuda else "cpu")
n_gpu = torch.cuda.device_count()
os.makedirs(args.output_dir, exist_ok=True)

In [14]:
len(train_bag)

145902

In [15]:
len(train_bag_neg)

47441

In [16]:
train_bag_neg[100]

('Nationen Nationen is not norwegian newspaper with particular focus on agriculture',
 'P407',
 'Nationen Nationen',
 'particular focus on agriculture',
 -1)

In [17]:
maskingprob = 0.9
indexed_tokens_all = []
segments_ids_all = []
input_mask_all = []
kb_rel_id_all = []
OIE_ent_label_all = []
negflag_all = []

max_seq = args.max_seq_length

for ins in tqdm(train_bag + train_bag_neg):
    (text, rel, ent1, ent2, negflag) = ins
    text = "[CLS] " + text + " [SEP]"
    tokenized_text = tokenizer.tokenize(text)
    tokenized_ent1 = tokenizer.tokenize(ent1)
    tokenized_ent2 = tokenizer.tokenize(ent2)
    pos1 = subfinder(tokenized_text, tokenized_ent1)
    pos2 = subfinder(tokenized_text, tokenized_ent2)
    
    if (not pos1) or (not pos2):
        continue
    
    if len(tokenized_text) > max_seq:
        continue
    
    indexed_tokens = tokenizer.convert_tokens_to_ids(tokenized_text)
    segments_ids = [0] * len(indexed_tokens)
    input_mask = [1] * len(indexed_tokens)
    
    #if len(indexed_tokens) > max_seq:
        #continue
    
    while len(indexed_tokens) < max_seq:
        indexed_tokens.append(0)
        segments_ids.append(0)
        input_mask.append(0)
    
    
    OIE_ent_label = [0] * max_seq
    
    randn = random.random()
    for idxp1 in pos1:
        (p1_s, p1_e) = idxp1
        for i in range(p1_s,p1_e):
            OIE_ent_label[i] = 1
            if (randn < maskingprob):
                indexed_tokens[i] = 100
    
    randn = random.random()
    for idxp2 in pos2:
        (p2_s, p2_e) = idxp2
        for i in range(p2_s,p2_e):
            OIE_ent_label[i] = 1
            if (randn < maskingprob):
                indexed_tokens[i] = 100
    
    
    indexed_tokens_all.append(indexed_tokens)
    segments_ids_all.append(segments_ids)
    input_mask_all.append(input_mask)
    kb_rel_id_all.append(rel)
    OIE_ent_label_all.append(OIE_ent_label)
    negflag_all.append([negflag])

indexed_tokens_all_tensor = torch.tensor([f for f in indexed_tokens_all], dtype=torch.long)
segments_ids_all_tensor = torch.tensor([f for f in segments_ids_all], dtype=torch.long)
input_mask_all_tensor = torch.tensor([f for f in input_mask_all], dtype=torch.long)
ent_label_all_tensor = torch.tensor([f for f in OIE_ent_label_all], dtype=torch.float)
negflag_all_tensor = torch.tensor([f for f in negflag_all], dtype=torch.float)

100%|██████████| 193277/193277 [01:22<00:00, 2340.88it/s]


In [18]:
kb_rel_id_all_tensor = torch.tensor([relid2idx[f] for f in kb_rel_id_all], dtype=torch.long)
train_data = TensorDataset(indexed_tokens_all_tensor, segments_ids_all_tensor, input_mask_all_tensor, kb_rel_id_all_tensor, ent_label_all_tensor, negflag_all_tensor)
train_sampler = RandomSampler(train_data)
train_dataloader = DataLoader(train_data, sampler=train_sampler, batch_size=args.train_batch_size)

In [19]:
model = BertForEntityandRelation_entrelsametime_ver2_negsen_last.from_pretrained(args.bert_model, cache_dir=PYTORCH_PRETRAINED_BERT_CACHE / 'distributed_{}'.format(args.local_rank), rel_dim = args.rel_dim, max_tok = args.max_seq_length)

In [20]:
model.to(device)
param_optimizer = list(model.named_parameters())
param_optimizer = [n for n in param_optimizer if 'pooler' not in n[0]]
no_decay = ['bias', 'LayerNorm.bias', 'LayerNorm.weight']
optimizer_grouped_parameters = [{'params': [p for n, p in param_optimizer if not any(nd in n for nd in no_decay)], 'weight_decay': 0.01},{'params': [p for n, p in param_optimizer if any(nd in n for nd in no_decay)], 'weight_decay': 0.0}]
num_train_optimization_steps = int(len(indexed_tokens_all_tensor) / args.train_batch_size / args.gradient_accumulation_steps) * args.num_train_epochs
optimizer = BertAdam(optimizer_grouped_parameters,lr=args.learning_rate,warmup=args.warmup_proportion,t_total=num_train_optimization_steps)

In [21]:
model.train()

BertForEntityandRelation_entrelsametime_ver2_negsen_last(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768, padding_idx=0)
      (token_type_embeddings): Embedding(2, 768, padding_idx=0)
      (LayerNorm): BertLayerNorm()
      (dropout): Dropout(p=0.1)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): BertLayerNorm()
              (dropout): Dropou

In [22]:
global_step = 0

In [23]:
for _ in trange(int(args.num_train_epochs), desc="Epoch"):
    for step, batch in enumerate(tqdm(train_dataloader, desc="Iteration")):
        if n_gpu == 1:
            batch = tuple(t.to(device) for t in batch)
        indexed_tokens_all_tensor_train, segments_ids_all_tensor_train, input_mask_all_tensor_train, kb_rel_id_all_tensor_train, ent_label_tensor_train, negflag_all_tensor = batch
        
        kb_rel_list = kb_rel_id_all_tensor_train.data.cpu().numpy()
        kb_rel_id_list = [idx2relid[f] for f in kb_rel_list]
        kb_rel_emb_tensor_train = torch.tensor([kb_id2emb[f] for f in kb_rel_id_list]).to('cuda')
        
        loss_r, loss_e = model(indexed_tokens_all_tensor_train, segments_ids_all_tensor_train, input_mask_all_tensor_train, kb_rel_emb_tensor_train, ent_label_tensor_train, negflag_all_tensor)
        loss = loss_r + loss_e
        loss.backward()
        if (step + 1) % args.gradient_accumulation_steps == 0:
            optimizer.step()
            optimizer.zero_grad()
            global_step += 1

    model_to_save = model.module if hasattr(model, 'module') else model
    output_model_file = os.path.join(args.output_dir, "pytorch_model" + str(_) + ".bin")
    torch.save(model_to_save.state_dict(), output_model_file)
    

Iteration:   1%|▏         | 240/18472 [01:02<1:18:33,  3.87it/s]


Iteration:   3%|▎         | 480/18472 [02:04<1:17:47,  3.85it/s]


Iteration:   4%|▍         | 720/18472 [03:07<1:17:00,  3.84it/s]


Iteration:   5%|▌         | 960/18472 [04:09<1:16:19,  3.82it/s]


Iteration:   6%|▋         | 1197/18472 [05:11<1:14:54,  3.84it/s]


...

Iteration:  96%|█████████▌| 17754/18472 [1:17:02<03:07,  3.84it/s]


Iteration:  97%|█████████▋| 17988/18472 [1:18:03<02:06,  3.84it/s]


Iteration:  99%|█████████▊| 18222/18472 [1:19:04<01:05,  3.84it/s]


Iteration: 100%|█████████▉| 18456/18472 [1:20:05<00:04,  3.84it/s]


Iteration: 100%|█████████▉| 18470/18472 [1:20:09<00:00,  3.84it/s]Training beyond specified 't_total' steps with schedule 'warmup_linear'. Learning rate set to 0.0. Please set 't_total' of BertAdam correctly.

Iteration: 100%|█████████▉| 18471/18472 [1:20:09<00:00,  3.84it/s]Training beyond specified 't_total' steps with schedule 'warmup_linear'. Learning rate set to 0.0. Please set 't_total' of BertAdam correctly.

Epoch: 100%|██████████| 3/3 [4:00:34<00:00, 4810.97s/it]  .09it/s]


In [24]:
model_to_save = model.module if hasattr(model, 'module') else model
output_model_file = os.path.join(args.output_dir, "pytorch_model.bin")
torch.save(model_to_save.state_dict(), output_model_file)

In [24]:
output_config_file = os.path.join(args.output_dir, "config")
with open(output_config_file, 'w') as f:
    f.write(model_to_save.config.to_json_string())

In [12]:
output_model_file = os.path.join(args.output_dir, "pytorch_model0.bin")
model_state_dict = torch.load(output_model_file)
model = BertForEntityandRelation_entrelsametime_ver2_negsen_last.from_pretrained(args.bert_model, state_dict=model_state_dict, rel_dim = args.rel_dim, max_tok = args.max_seq_length)

In [17]:
output_config_file = os.path.join(args.output_dir, "config")
output_model_file = os.path.join(args.output_dir, "pytorch_model1.bin")
config = BertConfig(output_config_file)
model = BertForEntityandRelation_entrelsametime_ver2_negsen(config, rel_dim = args.rel_dim, max_tok = args.max_seq_length)
model.load_state_dict(torch.load(output_model_file))

In [236]:
####eval

In [35]:
indexed_tokens_all_eval = []
segments_ids_all_eval = []
input_mask_all_eval = []
kb_rel_id_all_eval = []
OIE_ent_label_all_eval = []
negflag_all_eval = []

max_seq = args.max_seq_length

for ins in tqdm(dev_bag):
    
    (text, rel, ent1, ent2, negflag) = ins
    text = "[CLS] " + text + " [SEP]"
    tokenized_text = tokenizer.tokenize(text)
    tokenized_ent1 = tokenizer.tokenize(ent1)
    tokenized_ent2 = tokenizer.tokenize(ent2)
    pos1 = subfinder(tokenized_text, tokenized_ent1)
    pos2 = subfinder(tokenized_text, tokenized_ent2)
    
    if (not pos1) or (not pos2):
        continue
    
    if len(tokenized_text) > max_seq:
        continue
    
    indexed_tokens = tokenizer.convert_tokens_to_ids(tokenized_text)
    segments_ids = [0] * len(indexed_tokens)
    input_mask = [1] * len(indexed_tokens)
    
    #if len(indexed_tokens) > max_seq:
        #continue
    
    while len(indexed_tokens) < max_seq:
        indexed_tokens.append(0)
        segments_ids.append(0)
        input_mask.append(0)
    
    OIE_ent_label = [0] * max_seq
    for idxp1 in pos1:
        (p1_s, p1_e) = idxp1
        for i in range(p1_s,p1_e):
            OIE_ent_label[i] = 1
        
    for idxp2 in pos2:
        (p2_s, p2_e) = idxp2
        for i in range(p2_s,p2_e):
            OIE_ent_label[i] = 1
    
    indexed_tokens_all_eval.append(indexed_tokens)
    segments_ids_all_eval.append(segments_ids)
    input_mask_all_eval.append(input_mask)
    kb_rel_id_all_eval.append(rel)
    OIE_ent_label_all_eval.append(OIE_ent_label)
    negflag_all_eval.append([negflag])

indexed_tokens_all_tensor_eval = torch.tensor([f for f in indexed_tokens_all_eval], dtype=torch.long)
segments_ids_all_tensor_eval = torch.tensor([f for f in segments_ids_all_eval], dtype=torch.long)
input_mask_all_tensor_eval = torch.tensor([f for f in input_mask_all_eval], dtype=torch.long)
ent_label_all_tensor_eval = torch.tensor([f for f in OIE_ent_label_all_eval], dtype=torch.float)
negflag_all_tensor_eval = torch.tensor([f for f in negflag_all_eval], dtype=torch.float)

100%|██████████| 55601/55601 [00:27<00:00, 2018.55it/s]


In [36]:
kb_rel_id_all_tensor_eval = torch.tensor([relid2idx[f] for f in kb_rel_id_all_eval], dtype=torch.long)
eval_data = TensorDataset(indexed_tokens_all_tensor_eval, segments_ids_all_tensor_eval, input_mask_all_tensor_eval, kb_rel_id_all_tensor_eval, ent_label_all_tensor_eval,negflag_all_tensor_eval)
eval_sampler = SequentialSampler(eval_data)
eval_dataloader = DataLoader(eval_data, sampler=eval_sampler, batch_size=1)

In [37]:
model.eval()

BertForEntityandRelation_entrelsametime_ver2_negsen(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768, padding_idx=0)
      (token_type_embeddings): Embedding(2, 768, padding_idx=0)
      (LayerNorm): BertLayerNorm()
      (dropout): Dropout(p=0.1)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): BertLayerNorm()
              (dropout): Dropout(p=0

In [38]:
model.to(device)

BertForEntityandRelation_entrelsametime_ver2_negsen(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768, padding_idx=0)
      (token_type_embeddings): Embedding(2, 768, padding_idx=0)
      (LayerNorm): BertLayerNorm()
      (dropout): Dropout(p=0.1)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): BertLayerNorm()
              (dropout): Dropout(p=0

In [39]:
relid_dict_count = {}
relid_dict_loss = {}
relid_dict_avage_loss = {}

relid_dict_loss_r = {}
relid_dict_avage_loss_r = {}


for idx in idx2relid:
    relid_dict_count[idx2relid[idx]] = 0
    relid_dict_loss[idx2relid[idx]] = 0
    relid_dict_avage_loss[idx2relid[idx]] = 0
    
    relid_dict_loss_r[idx2relid[idx]] = 0
    relid_dict_avage_loss_r[idx2relid[idx]] = 0

In [40]:
loss_eval = 0
loss_eval_r = 0
loss_eval_e = 0
eval_step = 0
for step, batch in enumerate(tqdm(eval_dataloader, desc="Iteration")):
    batch = tuple(t.to(device) for t in batch)
    indexed_tokens_all_tensor_eval, segments_ids_all_tensor_eval, input_mask_all_tensor_eval, kb_rel_id_all_tensor_eval, ent_label_all_tensor_eval,negflag_all_tensor_eval = batch
    
    kb_rel_list_eval = kb_rel_id_all_tensor_eval.data.cpu().numpy()
    kb_rel_id_list_eval = [idx2relid[f] for f in kb_rel_list_eval]
    kb_rel_emb_tensor_eval = torch.tensor([kb_id2emb[f] for f in kb_rel_id_list_eval]).to('cuda')
    
    loss_r, loss_e = model(indexed_tokens_all_tensor_eval, segments_ids_all_tensor_eval, input_mask_all_tensor_eval, kb_rel_emb_tensor_eval, ent_label_all_tensor_eval,negflag_all_tensor_eval)
    loss = loss_r + loss_e
    
    loss_value_r = loss_r.data.cpu().numpy()
    loss_value_e = loss_e.data.cpu().numpy()
    loss_value = loss.data.cpu().numpy()
    
    loss_eval+= loss_value
    loss_eval_r+=loss_value_r
    loss_eval_e+=loss_value_e
    
    eval_step += 1
    
    relid = kb_rel_id_list_eval[0]
    relid_dict_count[relid] +=1
    relid_dict_loss[relid] += loss_value
    relid_dict_loss_r[relid] += loss_value_r
    
loss_eval = loss_eval / eval_step
loss_eval_r = loss_eval_r / eval_step
loss_eval_e = loss_eval_e / eval_step

Iteration: 100%|██████████| 52144/52144 [13:03<00:00, 66.54it/s]


In [30]:
for relid in relid_dict_count:
    if relid_dict_count[relid] == 0:
        relid_dict_avage_loss[relid] = -1
        relid_dict_avage_loss_r[relid] = -1
    else:
        relid_dict_avage_loss[relid] = relid_dict_loss[relid] / relid_dict_count[relid]
        relid_dict_avage_loss_r[relid] = relid_dict_loss_r[relid] / relid_dict_count[relid]

In [43]:
loss_eval

0.4767223594408865

In [ ]:
#epoch 0 (last layer)
'''
loss_eval: 0.5163443235913238
loss_eval_r: 0.46008390708425584
loss_eval_e: 0.05626041643700869
'''

#epoch 1
'''
loss_eval: 0.47256814339469655
loss_eval_r: 0.42080627364407625
loss_eval_e: 0.05176186972449862
'''

#epoch 1
'''
loss_eval: 0.4767223594408865
loss_eval_r: 0.4262850733954059
loss_eval_e: 0.05043728612174976
'''

In [ ]:
#epoch 0 (second last layer)
'''
loss_eval: 0.5298702590257433
loss_eval_r: 0.46880159731174187
loss_eval_e: 0.061068661741032294
'''

#epoch 1
'''
loss_eval: 0.5028501149274656
loss_eval_r: 0.44900801904965754
loss_eval_e: 0.05384209593371701
'''

#epoch 1
'''
loss_eval: 0.502250441957688
loss_eval_r: 0.44834012929018846
loss_eval_e: 0.053910312659862306
'''

In [48]:
relid_dict_avage_loss

{'P31': 0.5283624978297076,
 'P17': 0.3461431473877424,
 'P27': 0.49567524544061853,
 'P106': 0.33600877379890115,
 'P131': 0.28575515001040097,
 'P19': 0.5151606040278705,
 'P47': 0.15138386187131858,
 'P54': 0.2545979611741172,
 'P161': 0.3700436647263689,
 'P105': 0.12956608288712096,
 'P641': 0.15909690693456274,
 'P20': 0.5208641999715368,
 'P171': 0.46682856185361743,
 'P1344': 0.05112777239046638,
 'P150': 0.13716494222384065,
 'P136': 0.7516525128369473,
 'P1412': 0.6313505634280895,
 'P69': 0.473886828067211,
 'P166': 0.8417384116159331,
 'P495': 0.6815217013066573,
 'P155': 0.7639875044464594,
 'P156': 0.6196366464903232,
 'P364': 0.4024268120962789,
 'P413': 0.034476964903764264,
 'P190': -1,
 'P279': 0.6063897222609205,
 'P421': 0.21859946846961975,
 'P175': 0.14224232770642295,
 'P361': 0.7347446056604385,
 'P264': 0.4398039899909995,
 'P40': 0.6080088377319356,
 'P102': 0.18953322290425773,
 'P57': 0.3019796825749204,
 'P3373': 0.4459517636446119,
 'P39': 0.50470727061351

In [65]:
import operator
sortedcountdict = sorted(relid_dict_avage_loss_r.items(), key=operator.itemgetter(1),reverse=True)

In [66]:
sortedcountdict

[('P407', 2.519871910750429),
 ('P50', 1.6534869149327278),
 ('P793', 1.204360681395346),
 ('P735', 1.1178084667772055),
 ('P750', 1.0578895246694378),
 ('P1040', 1.0370873041258526),
 ('P921', 0.9908880080495562),
 ('P1376', 0.9323155088772419),
 ('P101', 0.9284469734795416),
 ('P800', 0.8723263784601879),
 ('P119', 0.8340581065297303),
 ('P495', 0.7372643382110694),
 ('P155', 0.7166813475341194),
 ('P361', 0.6965628926753997),
 ('P170', 0.6934003577704596),
 ('P527', 0.661078172097416),
 ('P551', 0.657992256311898),
 ('P166', 0.6509988712777774),
 ('P186', 0.6435633018368581),
 ('P61', 0.6367196266301313),
 ('P40', 0.6357042149510435),
 ('P136', 0.6203152237031397),
 ('P1412', 0.6081742457076926),
 ('P36', 0.6067163848307429),
 ('P25', 0.6046760120898446),
 ('P937', 0.5964708931411907),
 ('P156', 0.5788161463063696),
 ('P19', 0.5677730915872947),
 ('P272', 0.5446817439683745),
 ('P162', 0.5377867352307245),
 ('P22', 0.5315056282181628),
 ('P180', 0.5309058725833893),
 ('P86', 0.51952

In [37]:
#eval에 이거 쓰자

In [191]:
text = "[CLS] Europe is a continent located entirely in the Northern Hemisphere and mostly in the Eastern Hemisphere. [SEP]"

In [120]:
text = "[CLS] Europe is a located entirely in the Northern Hemisphere and mostly in the Eastern Hemisphere. [SEP]"

In [216]:
text = "[CLS] Seoul is located in Gyeonggido. [SEP]"

In [18]:
text = "[CLS] Apples are sweet and edible fruits. [SEP]"

In [30]:
text = "[CLS] Apples have been grown for thousands of years in Asia and Europe. [SEP]"

In [54]:
text = "[CLS] Apples are sweet and edible fruits, and have been grown for thousands of years in Asia and Europe. [SEP]"

In [217]:
KB_relid = "P31"

In [218]:
tokenized_text = tokenizer.tokenize(text)
indexed_tokens = tokenizer.convert_tokens_to_ids(tokenized_text)
segments_ids = [0] * len(indexed_tokens)
input_mask = [1] * len(indexed_tokens)
OIE_label = [0] * len(indexed_tokens)

max_seq = args.max_seq_length
while len(indexed_tokens) < max_seq:
    indexed_tokens.append(0)
    segments_ids.append(0)
    input_mask.append(0)
    OIE_label.append(0)

In [219]:
tokenized_text

['[CLS]',
 'seoul',
 'is',
 'located',
 'in',
 'g',
 '##ye',
 '##ong',
 '##gi',
 '##do',
 '.',
 '[SEP]']

In [201]:
indexed_tokens[1] = 100

In [220]:
tokens_tensor = torch.tensor([indexed_tokens])
segments_tensors = torch.tensor([segments_ids])
input_mask_tensors = torch.tensor([input_mask])
OIE_label_tensors = torch.tensor([OIE_label], dtype=torch.float)

In [221]:
#unk = 100

In [222]:
#tokens_tensor = tokens_tensor.to('cuda')
#segments_tensors = segments_tensors.to('cuda')
#input_mask_tensors = input_mask_tensors.to('cuda')
#OIE_label_tensors = OIE_label_tensors.to('cuda')
model.eval()
#model.to('cuda')

BertForEntityandRelation_entrelsametime_ver2_negsen(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768, padding_idx=0)
      (token_type_embeddings): Embedding(2, 768, padding_idx=0)
      (LayerNorm): BertLayerNorm()
      (dropout): Dropout(p=0.1)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): BertLayerNorm()
              (dropout): Dropout(p=0

In [223]:
kb_test = kb_id2emb[KB_relid]
kb_test_tensor = torch.tensor([kb_test])
#kb_test_tensor = kb_test_tensor.to('cuda')

In [224]:
with torch.no_grad():
    rel, ent = model(tokens_tensor, segments_tensors, input_mask_tensors, kb_test_tensor, OIE_label_tensors)

In [225]:
entity = ent.data.cpu().numpy()

In [226]:
relation = rel.data.cpu().numpy()

In [29]:
relation_apple1_last = relation

In [41]:
relation_apple2_last = relation

In [53]:
relation_apple3_last = relation

In [68]:
relation_apple3_last_mask = relation

In [71]:
cos_sim(relation_apple1_last[0],relation_apple2_last[0])

0.25036132

In [72]:
cos_sim(relation_apple1_last[0],relation_apple3_last[0])

0.25056097

In [73]:
cos_sim(relation_apple2_last[0],relation_apple3_last[0])

0.9998092

In [74]:
cos_sim(relation_apple1_last[0],relation_apple3_last_mask[0])

0.3065261

In [75]:
cos_sim(relation_apple2_last[0],relation_apple3_last_mask[0])

0.3197614

In [88]:
relation_euno_last = relation

In [101]:
relation_eumask_last = relation

In [119]:
relation_euhemmask_last = relation

In [137]:
relation_euallmask_last = relation

In [149]:
relation_euno_last_con = relation

In [172]:
relation_eumask_last_con = relation

In [190]:
relation_euhemmask_last_con = relation

In [209]:
relation_euallmask_last_con = relation

In [227]:
relation_seoul = relation

In [210]:
cos_sim(relation_euno_last[0],relation_eumask_last[0])

0.428084

In [211]:
cos_sim(relation_euno_last[0],relation_euhemmask_last[0])

0.58632535

In [212]:
cos_sim(relation_euno_last[0],relation_euallmask_last[0])

0.58632535

In [213]:
cos_sim(relation_euno_last_con[0],relation_eumask_last_con[0])

0.62931305

In [214]:
cos_sim(relation_euno_last_con[0],relation_euhemmask_last_con[0])

0.9703095

In [215]:
cos_sim(relation_euno_last_con[0],relation_euallmask_last_con[0])

0.93983763

In [228]:
cos_sim(relation_seoul[0],relation_euno_last[0])

0.31382862

In [229]:
cos_sim(relation_seoul[0],relation_eumask_last[0])

0.4263263

In [230]:
cos_sim(relation_seoul[0],relation_euhemmask_last[0])

0.9159741

In [231]:
cos_sim(relation_seoul[0],relation_euallmask_last[0])

0.9159741

In [232]:
cos_sim(relation_seoul[0],relation_euno_last_con[0])

0.27751505

In [233]:
cos_sim(relation_seoul[0],relation_eumask_last_con[0])

0.43544558

In [234]:
cos_sim(relation_seoul[0],relation_euhemmask_last_con[0])

0.4456641

In [235]:
cos_sim(relation_seoul[0],relation_euallmask_last_con[0])

0.45651165

In [ ]:
#####

In [25]:
relation_apple1 = relation

In [36]:
relation_apple2 = relation

In [48]:
relation_apple3 = relation

In [68]:
relation_apple3_mask = relation

In [82]:
relation_eunomask = relation

In [95]:
relation_eumask = relation

In [112]:
relation_euhemmask = relation

In [146]:
relation_euallmask = relation

In [160]:
relation_seoul = relation

In [175]:
relation_eunomask_con = relation

In [187]:
relation_eumask_con = relation

In [204]:
relation_euhemmask_con = relation

In [222]:
relation_euallmask_con = relation

In [51]:
cos_sim(relation_apple1[0],relation_apple2[0])

0.28943363

In [52]:
cos_sim(relation_apple1[0],relation_apple3[0])

0.5040689

In [53]:
cos_sim(relation_apple2[0],relation_apple3[0])

0.9673797

In [69]:
cos_sim(relation_apple1[0],relation_apple3_mask[0])

0.5081114

In [70]:
cos_sim(relation_apple2[0],relation_apple3_mask[0])

0.40261555

In [147]:
cos_sim(relation_eunomask[0],relation_eumask[0])

0.8941533

In [148]:
cos_sim(relation_eunomask[0],relation_euhemmask[0])

0.86416936

In [149]:
cos_sim(relation_eunomask[0],relation_euallmask[0])

0.6431913

In [163]:
cos_sim(relation_seoul[0],relation_eunomask[0])

0.54931504

In [161]:
cos_sim(relation_seoul[0],relation_eumask[0])

0.5325559

In [162]:
cos_sim(relation_seoul[0],relation_euhemmask[0])

0.79063666

In [164]:
cos_sim(relation_seoul[0],relation_euallmask[0])

0.96650165

In [223]:
cos_sim(relation_seoul[0],relation_eunomask_con[0])

0.40459654

In [224]:
cos_sim(relation_seoul[0],relation_eumask_con[0])

0.416936

In [225]:
cos_sim(relation_seoul[0],relation_euhemmask_con[0])

0.35839957

In [226]:
cos_sim(relation_seoul[0],relation_euallmask_con[0])

0.37015387

In [26]:
from scipy.special import softmax
import numpy

In [50]:
kb_num_emb = numpy.asarray(kb_test)

In [70]:
import numpy
from numpy import dot
from numpy.linalg import norm
from scipy.spatial import distance

def cos_sim(A, B):
    return dot(A, B)/(norm(A)*norm(B))
def euclidean_dis(A, B):
    return distance.euclidean(A, B)
def mahalanobis_dis(A,B):
    V = numpy.cov(numpy.array([A, B]).T)
    IV = numpy.linalg.pinv(V)
    return distance.mahalanobis(A, B, IV)
def minkowski_dis (A,B):
    return distance.minkowski(A,B,3)

In [126]:
mahalanobis_dis(apple_s1, word_emb[0][127])

1.414213560434833

In [109]:
mahalanobis_dis(apple_s1, apple_s2)

1.4142135615385767

In [46]:
minkowski_dis([1, 0, 0], [0, 1, 0])

1.4142135623730951

In [553]:
cos_sim(relation_s2[0],relation_s4[0])

0.29151705

In [303]:
cos_sim(relation_fruit[0],relation_test_years_tokenandinputmod[0])

0.98690075

In [198]:
kb_sim_dict = {} #father 관계
for idx in kb_id2emb:
    kb_e_tmp = numpy.asarray(kb_id2emb[idx])
    kb_sim_dict[idx] = cos_sim(relation[0],kb_e_tmp)

In [199]:
import operator
sortedcountdict = sorted(kb_sim_dict.items(), key=operator.itemgetter(1),reverse=True)

In [200]:
sortedcountdict

[('P26', 0.7588279801380828),
 ('P40', 0.6156484462661017),
 ('P22', 0.6148132399049431),
 ('P3373', 0.5629720845018484),
 ('P112', 0.551599099548059),
 ('P161', 0.5514936043581695),
 ('P57', 0.5169887070645152),
 ('P162', 0.4715854629028565),
 ('P69', 0.4633191145424925),
 ('P800', 0.4477276319125965),
 ('P176', 0.4268754088044946),
 ('P1066', 0.4263742328156009),
 ('P50', 0.4010621573618344),
 ('P170', 0.39691709929535884),
 ('P509', 0.38262605265186733),
 ('P138', 0.38194773498616047),
 ('P735', 0.3748052500969454),
 ('P802', 0.37405940813712985),
 ('P1142', 0.36963183731739296),
 ('P86', 0.3646129761489008),
 ('P106', 0.35896265193119564),
 ('P527', 0.35397123685075355),
 ('P25', 0.33900415985605414),
 ('P39', 0.33628931835225717),
 ('P54', 0.3341664093951193),
 ('P241', 0.3282652079231972),
 ('P2416', 0.3263242101386728),
 ('P108', 0.3178543798123577),
 ('P437', 0.31180480395434007),
 ('P171', 0.299874659736874),
 ('P123', 0.29700650140345447),
 ('P61', 0.2960323183482476),
 ('P10

In [138]:
kb_sim_dict_nephew = {} #사촌 관계
for idx in kb_id2emb:
    kb_e_tmp = numpy.asarray(kb_id2emb[idx])
    kb_sim_dict_nephew[idx] = cos_sim(tmp_nephew[0],kb_e_tmp)

In [139]:
sortedcountdict_nephew = sorted(kb_sim_dict_nephew.items(), key=operator.itemgetter(1),reverse=True)